In [48]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import r2_score, mean_squared_error
import xgboost as xgb

In [47]:
! pip install xgboost

In [2]:
train=pd.read_csv(r"D:\Internship project\Project-Housing_splitted\test.csv",encoding='latin1')

In [3]:
test=pd.read_csv(r"D:\Internship project\Project-Housing_splitted\train.csv",encoding='latin1')

In [4]:
data=pd.concat([test,train])

In [7]:
data

Id  MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0     127         120       RL          NaN     4928   Pave   NaN      IR1   
1     889          20       RL         95.0    15865   Pave   NaN      IR1   
2     793          60       RL         92.0     9920   Pave   NaN      IR1   
3     110          20       RL        105.0    11751   Pave   NaN      IR1   
4     422          20       RL          NaN    16635   Pave   NaN      IR1   
..    ...         ...      ...          ...      ...    ...   ...      ...   
287    83          20       RL         78.0    10206   Pave   NaN      Reg   
288  1048          20       RL         57.0     9245   Pave   NaN      IR2   
289    17          20       RL          NaN    11241   Pave   NaN      IR1   
290   523          50       RM         50.0     5000   Pave   NaN      Reg   
291  1379         160       RM         21.0     1953   Pave   NaN      Reg   

    LandContour Utilities  ... PoolArea PoolQC  Fence MiscFeature MiscVal  \
0           Lvl    AllPub  ...        0    NaN    NaN         NaN       0   
1           Lvl    AllPub  ...        0    NaN    NaN         NaN       0   
2           Lvl    AllPub  ...        0    NaN    NaN         NaN       0   
3           Lvl    AllPub  ...        0    NaN  MnPrv         NaN       0   
4           Lvl    AllPub  ...        0    NaN    NaN         NaN       0   
..          ...       ...  ...      ...    ...    ...         ...     ...   
287         Lvl    AllPub  ...        0    NaN    NaN         NaN       0   
288         Lvl    AllPub  ...        0    NaN    NaN         NaN       0   
289         Lvl    AllPub  ...        0    NaN    NaN        Shed     700   
290         Lvl    AllPub  ...        0    NaN    NaN         NaN       0   
291         Lvl    AllPub  ...        0    NaN    NaN         NaN       0   

    MoSold YrSold  SaleType  SaleCondition  SalePrice  
0        2   2007        WD         Normal   128000.0  
1       10   2007        WD         Normal   268000.0  
2        6   2007        WD         Normal   269790.0  
3        1   2010       COD         Normal   190000.0  
4        6   2009        WD         Normal   215000.0  
..     ...    ...       ...            ...        ...  
287     10   2008        WD         Normal        NaN  
288      2   2008        WD         Normal        NaN  
289      3   2010        WD         Normal        NaN  
290     10   2006        WD         Normal        NaN  
291      6   2006        WD         Normal        NaN  

[1460 rows x 81 columns]

In [9]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1460 entries, 0 to 291
Data columns (total 81 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Id             1460 non-null   int64  
 1   MSSubClass     1460 non-null   int64  
 2   MSZoning       1460 non-null   object 
 3   LotFrontage    1201 non-null   float64
 4   LotArea        1460 non-null   int64  
 5   Street         1460 non-null   object 
 6   Alley          91 non-null     object 
 7   LotShape       1460 non-null   object 
 8   LandContour    1460 non-null   object 
 9   Utilities      1460 non-null   object 
 10  LotConfig      1460 non-null   object 
 11  LandSlope      1460 non-null   object 
 12  Neighborhood   1460 non-null   object 
 13  Condition1     1460 non-null   object 
 14  Condition2     1460 non-null   object 
 15  BldgType       1460 non-null   object 
 16  HouseStyle     1460 non-null   object 
 17  OverallQual    1460 non-null   int64  
 18  OverallCo

In [10]:
data.isnull().sum()

Id                 0
MSSubClass         0
MSZoning           0
LotFrontage      259
LotArea            0
                ... 
MoSold             0
YrSold             0
SaleType           0
SaleCondition      0
SalePrice        292
Length: 81, dtype: int64

In [13]:
data.describe()

Id   MSSubClass  LotFrontage        LotArea  OverallQual  \
count  1460.000000  1460.000000  1201.000000    1460.000000  1460.000000   
mean    730.500000    56.897260    70.049958   10516.828082     6.099315   
std     421.610009    42.300571    24.284752    9981.264932     1.382997   
min       1.000000    20.000000    21.000000    1300.000000     1.000000   
25%     365.750000    20.000000    59.000000    7553.500000     5.000000   
50%     730.500000    50.000000    69.000000    9478.500000     6.000000   
75%    1095.250000    70.000000    80.000000   11601.500000     7.000000   
max    1460.000000   190.000000   313.000000  215245.000000    10.000000   

       OverallCond    YearBuilt  YearRemodAdd   MasVnrArea   BsmtFinSF1  ...  \
count  1460.000000  1460.000000   1460.000000  1452.000000  1460.000000  ...   
mean      5.575342  1971.267808   1984.865753   103.685262   443.639726  ...   
std       1.112799    30.202904     20.645407   181.066207   456.098091  ...   
min       1.000000  1872.000000   1950.000000     0.000000     0.000000  ...   
25%       5.000000  1954.000000   1967.000000     0.000000     0.000000  ...   
50%       5.000000  1973.000000   1994.000000     0.000000   383.500000  ...   
75%       6.000000  2000.000000   2004.000000   166.000000   712.250000  ...   
max       9.000000  2010.000000   2010.000000  1600.000000  5644.000000  ...   

        WoodDeckSF  OpenPorchSF  EnclosedPorch    3SsnPorch  ScreenPorch  \
count  1460.000000  1460.000000    1460.000000  1460.000000  1460.000000   
mean     94.244521    46.660274      21.954110     3.409589    15.060959   
std     125.338794    66.256028      61.119149    29.317331    55.757415   
min       0.000000     0.000000       0.000000     0.000000     0.000000   
25%       0.000000     0.000000       0.000000     0.000000     0.000000   
50%       0.000000    25.000000       0.000000     0.000000     0.000000   
75%     168.000000    68.000000       0.000000     0.000000     0.000000   
max     857.000000   547.000000     552.000000   508.000000   480.000000   

          PoolArea       MiscVal       MoSold       YrSold      SalePrice  
count  1460.000000   1460.000000  1460.000000  1460.000000    1168.000000  
mean      2.758904     43.489041     6.321918  2007.815753  181477.005993  
std      40.177307    496.123024     2.703626     1.328095   79105.586863  
min       0.000000      0.000000     1.000000  2006.000000   34900.000000  
25%       0.000000      0.000000     5.000000  2007.000000  130375.000000  
50%       0.000000      0.000000     6.000000  2008.000000  163995.000000  
75%       0.000000      0.000000     8.000000  2009.000000  215000.000000  
max     738.000000  15500.000000    12.000000  2010.000000  755000.000000  

[8 rows x 38 columns]

In [5]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1460 entries, 0 to 291
Data columns (total 81 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Id             1460 non-null   int64  
 1   MSSubClass     1460 non-null   int64  
 2   MSZoning       1460 non-null   object 
 3   LotFrontage    1201 non-null   float64
 4   LotArea        1460 non-null   int64  
 5   Street         1460 non-null   object 
 6   Alley          91 non-null     object 
 7   LotShape       1460 non-null   object 
 8   LandContour    1460 non-null   object 
 9   Utilities      1460 non-null   object 
 10  LotConfig      1460 non-null   object 
 11  LandSlope      1460 non-null   object 
 12  Neighborhood   1460 non-null   object 
 13  Condition1     1460 non-null   object 
 14  Condition2     1460 non-null   object 
 15  BldgType       1460 non-null   object 
 16  HouseStyle     1460 non-null   object 
 17  OverallQual    1460 non-null   int64  
 18  OverallCo

In [6]:
drop_columns=['Id','MSSubClass','LotArea','Street','Alley','LotShape','LandContour','LotConfig','Neighborhood','Condition1','Condition2','BldgType','HouseStyle','OverallQual','RoofMatl','Exterior1st','Exterior2nd','MasVnrType','ExterQual','Foundation','BsmtQual','BsmtExposure','BsmtFinType1','BsmtFinSF1','BsmtFinType2','BsmtFinSF2','BsmtUnfSF','TotalBsmtSF','1stFlrSF','2ndFlrSF','LowQualFinSF','GrLivArea','BsmtFullBath','BsmtHalfBath','FullBath','HalfBath','BedroomAbvGr','KitchenAbvGr','TotRmsAbvGrd','FireplaceQu','GarageType','GarageYrBlt','GarageFinish','GarageCars','GarageQual','PavedDrive','WoodDeckSF',
             'WoodDeckSF','OpenPorchSF','EnclosedPorch','3SsnPorch','ScreenPorch','MiscFeature','MiscVal','MoSold','YrSold']

In [8]:
import matplotlib.pyplot as plt
import seaborn as sns
    
corr_mat=data.corr().abs()
plt.figure(figsize=[150,160])
sns.heatmap(corr_mat,annot=True,annot_kws= {'size':50})
plt.title("correlation Matrix")
plt.show()

In [9]:
data=data.drop(columns=drop_columns,axis=1)

In [10]:
data.shape

(1460, 26)

In [11]:
data.isna().sum()

MSZoning            0
LotFrontage       259
Utilities           0
LandSlope           0
OverallCond         0
YearBuilt           0
YearRemodAdd        0
RoofStyle           0
MasVnrArea          8
ExterCond           0
BsmtCond           37
Heating             0
HeatingQC           0
CentralAir          0
Electrical          1
KitchenQual         0
Functional          0
Fireplaces          0
GarageArea          0
GarageCond         81
PoolArea            0
PoolQC           1453
Fence            1179
SaleType            0
SaleCondition       0
SalePrice         292
dtype: int64

In [19]:
data.drop(columns='PoolQC',axis=1, inplace=True)

In [20]:
data.drop(columns='Fence', axis=1, inplace=True)

In [21]:
data.shape

(1460, 24)

In [22]:
data=data.dropna()
data.head(5)

MSZoning  LotFrontage Utilities LandSlope  OverallCond  YearBuilt  \
1       RL         95.0    AllPub       Mod            6       1970   
2       RL         92.0    AllPub       Gtl            5       1996   
3       RL        105.0    AllPub       Gtl            6       1977   
5       RL         58.0    AllPub       Gtl            5       2006   
7       RL         88.0    AllPub       Gtl            4       1957   

   YearRemodAdd RoofStyle  MasVnrArea ExterCond  ... Electrical KitchenQual  \
1          1970      Flat         0.0        Gd  ...      SBrkr          Gd   
2          1997     Gable         0.0        TA  ...      SBrkr          TA   
3          1977       Hip       480.0        TA  ...      SBrkr          TA   
5          2006     Gable         0.0        TA  ...      SBrkr          Gd   
7          2000     Gable        67.0        TA  ...      SBrkr          TA   

  Functional Fireplaces GarageArea GarageCond PoolArea  SaleType  \
1        Typ          1        621         TA        0        WD   
2        Typ          1        455         TA        0        WD   
3        Typ          1        546         TA        0       COD   
5        Typ          1        660         TA        0       New   
7       Maj1          1        484         TA        0        WD   

   SaleCondition SalePrice  
1         Normal  268000.0  
2         Normal  269790.0  
3         Normal  190000.0  
5        Partial  219210.0  
7         Normal  155000.0  

[5 rows x 24 columns]

In [23]:
data.shape

(873, 24)

In [24]:
data.describe()

LotFrontage  OverallCond    YearBuilt  YearRemodAdd   MasVnrArea  \
count   873.000000   873.000000   873.000000    873.000000   873.000000   
mean     71.797251     5.605956  1972.104238   1985.902635   110.090493   
std      25.067869     1.092326    31.226891     21.032378   194.188874   
min      21.000000     2.000000  1880.000000   1950.000000     0.000000   
25%      60.000000     5.000000  1953.000000   1967.000000     0.000000   
50%      70.000000     5.000000  1974.000000   1995.000000     0.000000   
75%      81.000000     6.000000  2003.000000   2005.000000   168.000000   
max     313.000000     9.000000  2010.000000   2010.000000  1600.000000   

       Fireplaces   GarageArea    PoolArea      SalePrice  
count  873.000000   873.000000  873.000000     873.000000  
mean     0.617411   509.381443    3.768614  187914.454754  
std      0.637346   192.806904   45.549792   82529.099748  
min      0.000000   160.000000    0.000000   35311.000000  
25%      0.000000   380.000000    0.000000  133500.000000  
50%      1.000000   487.000000    0.000000  167240.000000  
75%      1.000000   612.000000    0.000000  225000.000000  
max      3.000000  1418.000000  648.000000  755000.000000

In [26]:
data.drop_duplicates(inplace=True)

In [27]:
data.shape

(873, 24)

In [29]:
data.columns.values.tolist()

['MSZoning',
 'LotFrontage',
 'Utilities',
 'LandSlope',
 'OverallCond',
 'YearBuilt',
 'YearRemodAdd',
 'RoofStyle',
 'MasVnrArea',
 'ExterCond',
 'BsmtCond',
 'Heating',
 'HeatingQC',
 'CentralAir',
 'Electrical',
 'KitchenQual',
 'Functional',
 'Fireplaces',
 'GarageArea',
 'GarageCond',
 'PoolArea',
 'SaleType',
 'SaleCondition',
 'SalePrice']

In [32]:
numeric=['int8','int16','int32','int64','float16','float32','float64']
categorical=[]
features=data.columns.values.tolist()

for col in features:
    if data[col].dtype in numeric:
        continue
    categorical.append(col)

In [33]:
categorical

['MSZoning',
 'Utilities',
 'LandSlope',
 'RoofStyle',
 'ExterCond',
 'BsmtCond',
 'Heating',
 'HeatingQC',
 'CentralAir',
 'Electrical',
 'KitchenQual',
 'Functional',
 'GarageCond',
 'SaleType',
 'SaleCondition']

In [34]:
df_dummies=pd.get_dummies(data[categorical],drop_first=True)

In [35]:
df_dummies.head()

MSZoning_FV  MSZoning_RH  MSZoning_RL  MSZoning_RM  LandSlope_Mod  \
1            0            0            1            0              1   
2            0            0            1            0              0   
3            0            0            1            0              0   
5            0            0            1            0              0   
7            0            0            1            0              0   

   LandSlope_Sev  RoofStyle_Gable  RoofStyle_Gambrel  RoofStyle_Hip  \
1              0                0                  0              0   
2              0                1                  0              0   
3              0                0                  0              1   
5              0                1                  0              0   
7              0                1                  0              0   

   RoofStyle_Mansard  ...  SaleType_ConLI  SaleType_ConLw  SaleType_New  \
1                  0  ...               0               0             0   
2                  0  ...               0               0             0   
3                  0  ...               0               0             0   
5                  0  ...               0               0             1   
7                  0  ...               0               0             0   

   SaleType_Oth  SaleType_WD  SaleCondition_AdjLand  SaleCondition_Alloca  \
1             0            1                      0                     0   
2             0            1                      0                     0   
3             0            0                      0                     0   
5             0            0                      0                     0   
7             0            1                      0                     0   

   SaleCondition_Family  SaleCondition_Normal  SaleCondition_Partial  
1                     0                     1                      0  
2                     0                     1                      0  
3                     0                     1                      0  
5                     0                     0                      1  
7                     0                     1                      0  

[5 rows x 52 columns]

In [36]:
data=data.join(df_dummies)

In [37]:
data

MSZoning  LotFrontage Utilities LandSlope  OverallCond  YearBuilt  \
1          RL         95.0    AllPub       Mod            6       1970   
2          RL         92.0    AllPub       Gtl            5       1996   
3          RL        105.0    AllPub       Gtl            6       1977   
5          RL         58.0    AllPub       Gtl            5       2006   
7          RL         88.0    AllPub       Gtl            4       1957   
...       ...          ...       ...       ...          ...        ...   
1157       RM         80.0    AllPub       Gtl            5       2003   
1160       RL         53.0    AllPub       Gtl            6       1977   
1162       RL         45.0    AllPub       Gtl            3       1914   
1165       RL         24.0    AllPub       Gtl            6       1976   
1166  C (all)         50.0    AllPub       Gtl            4       1920   

      YearRemodAdd RoofStyle  MasVnrArea ExterCond  ... SaleType_ConLI  \
1             1970      Flat         0.0        Gd  ...              0   
2             1997     Gable         0.0        TA  ...              0   
3             1977       Hip       480.0        TA  ...              0   
5             2006     Gable         0.0        TA  ...              0   
7             2000     Gable        67.0        TA  ...              0   
...            ...       ...         ...       ...  ...            ...   
1157          2004     Gable         0.0        TA  ...              0   
1160          1977     Gable         0.0        TA  ...              0   
1162          1950     Gable         0.0        Fa  ...              0   
1165          1976     Gable         0.0        TA  ...              0   
1166          1950   Gambrel         0.0        Fa  ...              0   

     SaleType_ConLw SaleType_New SaleType_Oth SaleType_WD  \
1                 0            0            0           1   
2                 0            0            0           1   
3                 0            0            0           0   
5                 0            1            0           0   
7                 0            0            0           1   
...             ...          ...          ...         ...   
1157              0            0            0           1   
1160              0            0            0           0   
1162              0            0            0           1   
1165              0            0            0           1   
1166              0            0            0           1   

     SaleCondition_AdjLand SaleCondition_Alloca  SaleCondition_Family  \
1                        0                    0                     0   
2                        0                    0                     0   
3                        0                    0                     0   
5                        0                    0                     0   
7                        0                    0                     0   
...                    ...                  ...                   ...   
1157                     0                    0                     0   
1160                     0                    0                     0   
1162                     0                    0                     0   
1165                     0                    0                     0   
1166                     0                    0                     0   

      SaleCondition_Normal SaleCondition_Partial  
1                        1                     0  
2                        1                     0  
3                        1                     0  
5                        0                     1  
7                        1                     0  
...                    ...                   ...  
1157                     1                     0  
1160                     0                     0  
1162                     1                     0  
1165                     1                     0  
1166                     1                     0  

[873

In [38]:
data.drop(columns=categorical,axis=1,inplace=True)

In [39]:
data

LotFrontage  OverallCond  YearBuilt  YearRemodAdd  MasVnrArea  \
1            95.0            6       1970          1970         0.0   
2            92.0            5       1996          1997         0.0   
3           105.0            6       1977          1977       480.0   
5            58.0            5       2006          2006         0.0   
7            88.0            4       1957          2000        67.0   
...           ...          ...        ...           ...         ...   
1157         80.0            5       2003          2004         0.0   
1160         53.0            6       1977          1977         0.0   
1162         45.0            3       1914          1950         0.0   
1165         24.0            6       1976          1976         0.0   
1166         50.0            4       1920          1950         0.0   

      Fireplaces  GarageArea  PoolArea  SalePrice  MSZoning_FV  ...  \
1              1         621         0   268000.0            0  ...   
2              1         455         0   269790.0            0  ...   
3              1         546         0   190000.0            0  ...   
5              1         660         0   219210.0            0  ...   
7              1         484         0   155000.0            0  ...   
...          ...         ...       ...        ...          ...  ...   
1157           0         440         0   140000.0            0  ...   
1160           0         440         0   140000.0            0  ...   
1162           0         200         0    58500.0            0  ...   
1165           1         440         0   148500.0            0  ...   
1166           0         250         0    40000.0            0  ...   

      SaleType_ConLI  SaleType_ConLw  SaleType_New  SaleType_Oth  SaleType_WD  \
1                  0               0             0             0            1   
2                  0               0             0             0            1   
3                  0               0             0             0            0   
5                  0               0             1             0            0   
7                  0               0             0             0            1   
...              ...             ...           ...           ...          ...   
1157               0               0             0             0            1   
1160               0               0             0             0            0   
1162               0               0             0             0            1   
1165               0               0             0             0            1   
1166               0               0             0             0            1   

      SaleCondition_AdjLand  SaleCondition_Alloca  SaleCondition_Family  \
1                         0                     0                     0   
2                         0                     0                     0   
3                         0                     0                     0   
5                         0                     0                     0   
7                         0                     0                     0   
...                     ...                   ...                   ...   
1157                      0                     0                     0   
1160                      0                     0                     0   
1162                      0                     0                     0   
1165                      0                     0                     0   
1166                      0                     0                     0   

      SaleCondition_Normal  SaleCondition_Partial  
1                        1                      0  
2                        1                      0  
3                        1                      0  
5                        0                      1  
7                        1                      0  
...                    ...                    ...  
1157                     1                      0  
1160      

In [40]:
data=data[data['SalePrice']>50000.0]

In [41]:
data.shape

(871, 61)

In [42]:
x=data.drop(['SalePrice'],axis=1)
y=data['SalePrice']

In [49]:
train_x, test_x, train_y, test_y= train_test_split(x,y, test_size=0.25, random_state=10)

In [50]:
xgb=xgb.XGBRegressor()

In [51]:
xgb.fit(train_x,train_y)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, gpu_id=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=None, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=None, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             n_estimators=100, n_jobs=None, num_parallel_tree=None,
             predictor=None, random_state=None, ...)

In [52]:
y_pred=xgb.predict(test_x)

In [55]:
r2_score(test_y,y_pred)

0.6138132023503813